In [1]:
import os

os.environ["HF_HOME"] = "/workspace/local-HF-cache/"
os.environ["HF_HUB_ENABLE_HF_TRANSFER"] = "1"


In [2]:
import torch

from textsum.utils import check_ampere_gpu
check_ampere_gpu() # automatically enables TF32 if Ampere+ available


NVIDIA GeForce RTX 4090 (compute capability 8.9) supports NVIDIA Ampere or later, enabled TF32 in PyTorch.


In [3]:
from datasets import load_dataset

# Login using e.g. `huggingface-cli login` to access this dataset
ds = load_dataset("pszemraj/scriptbase-pegX-summaries", "no-text-4beams")
ds

12/05/2024 05:46:29 INFO PyTorch version 2.4.1+cu124 available.


DatasetDict({
    train: Dataset({
        features: ['title', 'summary_official', 'metadata', 'source', 'summary_chunks', 'summary_generated'],
        num_rows: 1315
    })
})

In [4]:
import torch
from transformers import pipeline

pipe = pipeline(
    "text2text-generation",
    model="pszemraj/flan-t5-xl-summary-map-reduce-1024",
    device_map="auto",
)

# examples
text = """"Sangers on a Train" is a 1950 film about a train driver, Guy Haines, who discovers his wife, Miriam, has been murdered in Metcalf, Washington, DC. The film delves into the relationship between Guy and Anne Burton, focusing on Guy's desire for Anne to marry him.
"Screentalk" is a comedy about Anne Burton and her husband, Guy Haines, who are investigating the murder of their daughter, Miriam. The plot revolves around Anne's relationship with Bruno, who has been arrested for his wife's murder. In the second set, Guy and Anne meet at a tennis court in Washington, DC, where they plan to play against each other. Hennessy and Hammond investigate the crime scene, leading to Guy's arrest.
"The Announcer's Boom Forest Hills" is a tennis game between Guy Haines and Bruno Antony, with the score six-five. In the second set, Haines leads three games to four, but his opponent, Bernard Reynolds, attacks him in the third set. Meanwhile, Anne Hennessy and Barbara Hammond are preparing for dinner at the amusement park, where Guy has been waiting for hours. A police car arrives, followed by a taxi. The boatman and detectives follow Guy through the queue, leading to the conclusion that Guy was the man responsible for the accident."""

text = """A computer implemented method of generating a syntactic object. The method includes the steps of providing a plurality of input data sets, each input data set comprising one or more words, wherein each word is associated with at least one non-adjacent second word; creating an exocentric relationship between the first and second words by applying a neo-ian event semantics to the input data in such a way that the neo-antagonistic effect results in the generation of the syntactic object; and storing the generated syntactic object for future use.
    A method of learning and using language is disclosed. The method includes the steps of creating a lexicon of words, wherein each word in the lexicon has at least two possible states, selecting a set of one or more of the possible states of the lexicon to be used as a base state for a subsequent computational operation, and applying the computational operation to the base state to form a new output state.
    A computer implemented method for changing a first workspace to a second workspace. The method includes the steps of creating a new workspace by merging the first workspace with the second workspace, wherein the merging is based on at least one of: an impenetrable condition; a constraint on movement; and a resource restriction.
    The brain is constantly loosing neurons because you doesn&#39;t want all the junk around."""

# generate
if torch.cuda.is_available():
    torch.cuda.empty_cache()
with torch.autocast('cuda', dtype=torch.bfloat16):
    res = pipe(
    text,
    max_new_tokens=512, # increase up to 1024 if needed
    num_beams=4,
    early_stopping=True,
    truncation=True,
)
print(res[0]["generated_text"])


12/05/2024 05:46:32 INFO We will use 90% of the memory on device 0 for storing the model, and 10% for the buffer to avoid OOM. You can set `max_memory` in to a higher value to use more memory (at your own risk).


Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

tokenizer_config.json:   0%|          | 0.00/20.8k [00:00<?, ?B/s]

A computer-implemented method of generating a syntactic object involves providing input data sets containing one or more words, each associated with at least one non-adjacent second word, and creating an exocentric relationship between the words by applying neo-ian event semantics. This neo-antagonistic effect results in the generation of a syntactic object, which is then stored for future use. Additionally, a method of learning and using language involves creating a lexicon of words with at least two possible states, selecting a base state for a computational operation, and applying the computational operation to the base state to form a new output state. Furthermore, a computer-implemented method for changing workspaces involves merging two workspaces based on conditions such as an impenetrable condition, constraint on movement, or resource restriction.


In [7]:
pipe.model = torch.compile(pipe.model)

In [ ]:
def reduce_summary(example):
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
    with torch.autocast('cuda', dtype=torch.bfloat16, enabled=False):
        res = pipe(
        example['summary_chunks'],
        max_new_tokens=512, # increase up to 1024 if needed
        num_beams=4,
        early_stopping=True,
        truncation=True,
    )
    return {"summary_reduced_flanT5xl": res[0]["generated_text"]}

ds = ds.map(reduce_summary, batched=False)
ds

Map:   0%|          | 0/1315 [00:00<?, ? examples/s]

In [ ]:
# ds.push_to_hub("pszemraj/scriptbase-pegX-summaries", config_name="no-text-4beams-flanXL", 
#                commit_description='generate with pszemraj/flan-t5-xl-summary-map-reduce-1024')